In [191]:
import pandas as pd
#  Importing libraries and module and some setting for notebook

import pandas as pd
import re
from sklearn.feature_extraction.text import TfidfVectorizer
import numpy as np
from scipy.sparse import csr_matrix
import sparse_dot_topn.sparse_dot_topn as ct  #Cosine Similarity
import time
from tqdm import tqdm

In [192]:
def wikinorm(univ_string):
    from googlesearch import search
    from nltk.metrics import edit_distance
    from operator import itemgetter
    from numpy.random import default_rng
    rng = default_rng()
    results = search(univ_string, lang="en", num_results=3,advanced=True, sleep_interval=rng.uniform(1, 5))
    univ_name = univ_string.split(",")[0]
    u_results = [i.title for i in results if "Category:" not in i.title]
    return sorted([tuple((j,edit_distance(univ_name, j))) for j in u_results],key=itemgetter(1))[0][0]


In [193]:
def replace_uppercase_words(text):
    words = text.split()
    all_uppercase = all(word.isupper() for word in words)
    all_lowercase = all(word.islower() for word in words)
    if all_uppercase or all_lowercase:
        return text
    else:
        result = []
        for word in words:
            w = word.strip()
            if not w.isupper() and not w.islower():
                result.append(w)
        return " ".join(result).strip()

In [194]:
outdir="wos_processed_data"
univ = pd.read_excel(f"{outdir}/wos_institution_locations.xlsx")

from pandarallel import pandarallel
pandarallel.initialize(progress_bar=True, nb_workers=4)

univ["Institution_harm"] = univ["Institution"].parallel_apply(replace_uppercase_words)
print(len(univ))

INFO: Pandarallel will run on 4 workers.
INFO: Pandarallel will use standard multiprocessing data transfer (pipe) to transfer data between the main process and workers.

https://nalepae.github.io/pandarallel/troubleshooting/


155067


In [195]:
univ.sample(100)

UT (Unique WOS ID)                          Institution   
1094    WOS:000292330300050              Hong Kong Polytech Univ  \
21547   WOS:000374363900001               Guangdong Univ Technol   
53778   WOS:000459846300019                          Aarhus Univ   
153776  WOS:000907044000014                           Univ Siena   
81562   WOS:000554591602038  China Natl Elect Import Export Corp   
...                     ...                                  ...   
29206   WOS:000397047200002                  Univ Duisburg Essen   
21658   WOS:000374617600020                     Univ Southampton   
43289   WOS:000434742800004                     Univ Strathclyde   
37200   WOS:000418525100013                Goethe Univ Frankfurt   
95964   WOS:000616310200013               Eindhoven Univ Technol   

               Country                     Institution_harm  
1094             China              Hong Kong Polytech Univ  
21547            China               Guangdong Univ Technol  
53778          Denmark                          Aarhus Univ  
153776           Italy                           Univ Siena  
81562            China  China Natl Elect Import Export Corp  
...                ...                                  ...  
29206          Germany                  Univ Duisburg Essen  
21658   United Kingdom                     Univ Southampton  
43289   United Kingdom                     Univ Strathclyde  
37200          Germany                Goethe Univ Frankfurt  
95964      Netherlands               Eindhoven Univ Technol  

[100 rows x 4 columns]

In [196]:
univ_norm = univ.groupby("Country", as_index=False)["Institution_harm"].value_counts()
# univ_norm["search_for"] = univ_norm["Institution"]+", " + univ_norm["Country"]+ ", wikipedia"
univ_norm.sample(100)

Country                  Institution_harm  count
12655    Poland                     Space Res Ctr      6
12940  Portugal     Ctr Invest Energia State Grid      1
616       China              Minist Nat Resources     78
5561      China  PowerChina Huadong Engn Corp Ltd      1
514       China                    Chongqing Univ    478
...         ...                               ...    ...
476    Bulgaria                         Tech Univ      1
12454    Norway               Stavanger Univ Hosp      9
5489      China               Shanghai Sports Sch      1
768       China                        Hubei Univ     25
13527     Spain            Jimenez Diaz Univ Hosp      2

[100 rows x 3 columns]

In [197]:
# from pandarallel import pandarallel
# pandarallel.initialize(progress_bar=True, nb_workers=2)
#
# df_sample["search_result"] = df_sample["search_for"].parallel_apply(wikinorm)

In [198]:
def ngrams(string, n=3):

    string = re.sub(r'[,-./]|\sBD',r'', string)
    ngrams = zip(*[string[i:] for i in range(n)])
    return [''.join(ngram) for ngram in ngrams]

# calculate the similarity between two vectors of TF-IDF values the Cosine Similarity is usually used.
# result matrix in a very sparse terms and Scikit-learn deals with this nicely by returning a sparse CSR matrix.

def awesome_cossim_top(A, B, ntop, lower_bound=0):
    # force A and B as a CSR matrix.
    # If they have already been CSR, there is no overhead
    A = A.tocsr()
    B = B.tocsr()
    M, _ = A.shape
    _, N = B.shape

    idx_dtype = np.int32

    nnz_max = M*ntop

    indptr = np.zeros(M+1, dtype=idx_dtype)
    indices = np.zeros(nnz_max, dtype=idx_dtype)
    data = np.zeros(nnz_max, dtype=A.dtype)

    ct.sparse_dot_topn(
        M, N, np.asarray(A.indptr, dtype=idx_dtype),
        np.asarray(A.indices, dtype=idx_dtype),
        A.data,
        np.asarray(B.indptr, dtype=idx_dtype),
        np.asarray(B.indices, dtype=idx_dtype),
        B.data,
        ntop,
        lower_bound,
        indptr, indices, data)

    return csr_matrix((data,indices,indptr),shape=(M,N))

# unpacks the resulting sparse matrix

def get_matches_df(sparse_matrix, name_vector, top=None):
    non_zeros = sparse_matrix.nonzero()

    sparserows = non_zeros[0]
    sparsecols = non_zeros[1]

    if top:
        nr_matches = top
    else:
        nr_matches = sparsecols.size

    left_side = np.empty([nr_matches], dtype=object)
    right_side = np.empty([nr_matches], dtype=object)
    similarity = np.zeros(nr_matches)

    for index in range(0, nr_matches):
        left_side[index] = name_vector[sparserows[index]]
        right_side[index] = name_vector[sparsecols[index]]
        similarity[index] = sparse_matrix.data[index]

    return pd.DataFrame({'left_side': left_side,
                          'right_side': right_side,
                           'similarity': similarity})


def discrepancy_filter(df):
    f_df = df.copy()
    tokenlist = ["Med", "Hosp", "Tech", "Univ", "Acad", "Poly"]
    for token in tokenlist:
        f_df = f_df[~(((f_df["right_side"].str.contains(token))&
                       (~f_df["left_side"].str.contains(token)))
                      |
                ((f_df["left_side"].str.contains(token))&
                 (~f_df["right_side"].str.contains(token))))].copy()
    return f_df


# Define a function to get the high and low counts for each row
def get_high_low_counts(row):
    if row['left_count'] > row['right_count']:
        high_count = row['left_count']
        low_count = row['right_count']
    else: #row['left_count'] < row['right_count']:
        high_count = row['right_count']
        low_count = row['left_count']
    # else:
    #     if len(row['left_side']) > len(row['right_side']):
    #             high_count = len(row['left_side'])
    #             low_count = len(row['right_side'])
    #     else:
    #             high_count = len(row['right_side'])
    #             low_count = len(row['left_side'])
    return pd.Series([high_count, low_count])

In [199]:
merger = pd.DataFrame()

# for i in tqdm(filter(lambda c: c!="China", list(univ_norm["Country"].unique()))):
for i in tqdm(list(univ_norm["Country"].unique())):
    sub_inst = univ_norm[univ_norm["Country"]==i].reset_index()
    types = sub_inst['Institution_harm']
    vectorizer = TfidfVectorizer(min_df=1, analyzer=ngrams)
    tf_idf_matrix = vectorizer.fit_transform(types)
    t1 = time.time()
    matches = awesome_cossim_top(tf_idf_matrix, tf_idf_matrix.transpose(), 10, 0.8 if i!="China" else 0.9)
    t = time.time()-t1

    # store the  matches into new dataframe called matched_df and printing 10 samples
    matches_df = get_matches_df(matches, types)
    matches_df = matches_df[matches_df['similarity'] < 0.99999] # For removing all exact matches
    matches_df = discrepancy_filter(matches_df).reset_index(drop=True)
    matches_df["Country"] = i
    # matches_df = matches_df[pd.DataFrame(np.sort(matches_df[['left_side','right_side']].values,1)).duplicated()]
    # matches_df = matches_df[~matches_df[['left_side', 'right_side']].apply(frozenset, axis=1).duplicated()]
    merger = pd.concat([merger,matches_df], ignore_index=True)

for s in ["left","right"]:
    merger[f"{s}_count"] = merger[f"{s}_side"].apply(lambda x: len(univ[univ["Institution_harm"] == x]))

# Apply the function to create a new column
merger[['high_count', 'low_count']] = merger.apply(get_high_low_counts, axis=1)

# Use apply again to create the high_side and low_side columns
merger['high_side'] = merger.apply(lambda row: row['left_side'] if row['left_count'] > row['right_count'] else row['right_side'], axis=1)
merger['low_side'] = merger.apply(lambda row: row['left_side'] if row['left_count'] <= row['right_count'] else row['right_side'], axis=1)

# Drop the high_count and low_count columns if they are not needed
# merger.drop(['high_count', 'low_count'], axis=1, inplace=True)

100%|██████████| 31/31 [00:00<00:00, 32.89it/s]


In [200]:
fuzzymerger = merger[["Country","low_side","high_side","high_count","low_count","similarity"]].drop_duplicates()
fuzzymerger = fuzzymerger.sort_values(by=["low_side","high_count"], ascending=[True,False])
fuzzymerger = fuzzymerger.drop_duplicates(subset=["Country","low_side"]).sort_values(by="high_count", ascending=True).reset_index(drop=True)
print(len(fuzzymerger))
univ_harm = univ.copy()
univ_harm["merge_iter"] = 0
for i,row in tqdm(fuzzymerger.iterrows()):
    univ_harm.loc[((univ_harm["Country"]==row["Country"])&
                   (univ_harm["Institution_harm"]==row["low_side"])),"merge_iter"] += 1
    univ_harm.loc[((univ_harm["Country"]==row["Country"])&
                   (univ_harm["Institution_harm"]==row["low_side"])),"Institution_harm"] = row["high_side"]

1538


1538it [01:04, 23.79it/s]


In [201]:
# fuzzymerger[fuzzymerger["Country"]=="China"]

Country                                         low_side   
0      China  Logist Univ Chinese Peoples Armed Police Forces  \
9      China                  Flight Automat Control Res Inst   
10     China         Northwest Elect Power Design Inst Co Ltd   
11     China   Northwest Elect Power Design Inst Co Ltd China   
12     China           Northwest Inst Ecoenvironm & Resources   
...      ...                                              ...   
1531   China                      Chinese Univ Hong Kong Hong   
1532   China                       Huazhong Univ Sci & Techno   
1533   China                Hong Kong Polytech Univ Hong Kong   
1534   China                          Kong Kong Polytech Univ   
1537   China                    Univ Elect Sci & Technol Chin   

                                              high_side  high_count   
0        Logist Univ Chinese Peoples Armed Police Force           1  \
9                  Xian Flight Automat Control Res Inst           1   
10       Northwest Elect Power Design Inst Co Ltd China           1   
11             Northwest Elect Power Design Inst Co Ltd           1   
12    Northwest Inst Ecoenvironm & Resources Chinese Ac           1   
...                                                 ...         ...   
1531                             Chinese Univ Hong Kong         728   
1532                        Huazhong Univ Sci & Technol         729   
1533                            Hong Kong Polytech Univ         809   
1534                            Hong Kong Polytech Univ         809   
1537                     Univ Elect Sci & Technol China        1076   

      low_count  similarity  
0             1    0.988072  
9             1    0.905747  
10            1    0.926984  
11            1    0.926984  
12            1    0.910630  
...         ...         ...  
1531          1    0.935944  
1532          1    0.989260  
1533          1    0.917345  
1534          1    0.939416  
1537          1    0.983258  

[346 rows x 6 columns]

In [202]:
# univ_harm[((univ_harm["merge_iter"]>0) & (univ_harm["Country"]=="Italy"))]

UT (Unique WOS ID)                           Institution Country   
244     WOS:000286472300003                            Univ Trent   Italy  \
364     WOS:000287586100011                            Univ Trent   Italy   
410     WOS:000287939200011      Abdus Salam Int Ctr Theoret Phys   Italy   
765     WOS:000290996200002                            Univ Trent   Italy   
907     WOS:000291698400013                       INFN Sez Roma 1   Italy   
...                     ...                                   ...     ...   
153063  WOS:000900129900175        Univ Rome Campus Biomed Aquila   Italy   
154775  WOS:000929737300001                    Prevent & Res Inst   Italy   
154813  WOS:000929737300001                       Ist Super Sanit   Italy   
154855  WOS:000933331200004                       Univ Federio II   Italy   
154857  WOS:000933331200004  INAF Osservatorio Astron Capodimonte   Italy   

                         Institution_harm  merge_iter  
244                           Univ Trento           1  
364                           Univ Trento           1  
410     Abdus Salaam Int Ctr Theoret Phys           1  
765                           Univ Trento           1  
907                              Sez Roma           1  
...                                   ...         ...  
153063     Univ Rome Campus Biomed Aquila           2  
154775                 Prevent & Res Inst           2  
154813                   Ist Super Sanita           1  
154855                      Univ Federico           1  
154857          Osserv Astron Capodimonte           1  

[375 rows x 5 columns]

In [208]:
univ_harm.loc[((univ_harm["merge_iter"]>0) & (univ_harm["Country"]=="Italy")&
           (univ_harm["Institution"].str.lower().str.contains("sapien"))&
            (univ_harm["Institution"].str.lower().str.contains("univ"))), "Institution_harm"] = "Sapienza Univ Rome"

In [209]:
univ_harm[["Institution","Institution_harm"]].nunique()

Institution         17083
Institution_harm    14449
dtype: int64

In [210]:
univ_harm.to_excel(f"{outdir}/wos_institution_locations_harmonized.xlsx", index=False)